In [1]:
!nvidia-smi

Sat Jun  5 17:24:17 2021       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 465.27       Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   49C    P8     9W /  70W |      0MiB / 15109MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [2]:
!cp -r /content/drive/MyDrive/data_json .

In [3]:
!cp -r /content/drive/MyDrive/code .

In [4]:
!pip install sentencepiece

     |████████████████████████████████| 1.2MB 6.5MB/s 


In [5]:
!pip install -q git+https://github.com/huggingface/transformers.git

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 901kB 9.7MB/s 
     |████████████████████████████████| 3.3MB 54.1MB/s 


In [6]:
!pip install bertviz

     |████████████████████████████████| 153kB 8.0MB/s 
     |████████████████████████████████| 133kB 43.9MB/s 
     |████████████████████████████████| 81kB 13.0MB/s 
     |████████████████████████████████| 7.6MB 46.5MB/s 
ERROR: botocore 1.20.88 has requirement urllib3<1.27,>=1.25.4, but you'll have urllib3 1.24.3 which is incompatible.


In [7]:
from bertviz import head_view, model_view

In [8]:
import io
import os
import torch
from tqdm.notebook import tqdm
from torch.utils.data import Dataset, DataLoader
# from ml_things import plot_dict, plot_confusion_matrix, fix_text
from sklearn.metrics import classification_report, accuracy_score
from transformers import (set_seed,
                          TrainingArguments,
                          Trainer,
                          XLNetConfig,
                          XLNetTokenizer,
                          AdamW, 
                          get_linear_schedule_with_warmup,
                          XLNetForSequenceClassification)

In [9]:
import sys
sys.path.append('code')

In [10]:
import json

In [11]:
from SharedTaskDataset import SharedTaskDataset
from Gpt2ClassificationCollator import Gpt2ClassificationCollator

In [12]:
# Set seed for reproducibility.
set_seed(123)

# Number of training epochs (authors on fine-tuning Bert recommend between 2 and 4).
epochs = 4

# Number of batches - depending on the max sequence length and GPU memory.
# For 512 sequence length batch of 10 works without cuda memory issues.
# For small sequence length can try batch of 32 or higher.
batch_size = 1

# Pad or truncate text sequences to a specific length
# if `None` it will use maximum sequence of word piece tokens allowed by model.
max_length = 128 # 770 for concat

# Look for gpu to use. Will use `cpu` by default if no gpu found.
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# Name of transformers model - will use already pretrained model.
# Path of transformer model - will load your own model from local disk.
model_name_or_path = 'xlnet-base-cased'

# Dictionary of labels and their id - this will be used to convert.
# String labels to number ids.
with open('data_json/label_dict.json','r') as f:
  labels_ids = json.load(f)

# How many labels are we using in training.
# This is used to decide size of classification head.
n_labels = len(labels_ids)

# learning rate for the optimizer
lr_param = 2e-5

In [13]:
# Get model configuration.
print('Loading configuraiton...')
model_config = XLNetConfig.from_pretrained(pretrained_model_name_or_path=model_name_or_path, num_labels=n_labels)

# Get model's tokenizer.
print('Loading tokenizer...')
tokenizer = XLNetTokenizer.from_pretrained(pretrained_model_name_or_path=model_name_or_path)
# default to left padding
tokenizer.padding_side = "left"
# Define PAD Token = EOS Token = 50256
tokenizer.pad_token = tokenizer.eos_token


# Get the actual model.
print('Loading model...')
pretrained_path = '/content/drive/MyDrive/XLNet-best/lr_1e-05_best.pt'
model = XLNetForSequenceClassification.from_pretrained(pretrained_model_name_or_path=pretrained_path, config=model_config)

# resize model embedding to match new tokenizer
model.resize_token_embeddings(len(tokenizer))

# fix model padding token id
model.config.pad_token_id = model.config.eos_token_id

# Load model to defined device.
model.to(device)
print('Model loaded to `%s`'%device)

Loading configuraiton...



Loading tokenizer...



Loading model...
Model loaded to `cuda`


In [14]:
print('Dealing with Dev...')
# Create pytorch dataset.
dev_dataset =  SharedTaskDataset(path='data_json',
                                   split='dev')
print('Created `dev_dataset` with %d examples!'%len(dev_dataset))

Dealing with Dev...
Created `dev_dataset` with 3264 examples!


In [41]:
mins = 100
min_l = []
min_idx = []
for i in range(len(dev_dataset)):
  sentence = dev_dataset[i]['text']
  l = len(sentence)
  if l < mins:
    min_l.append(l)
    min_idx.append(i)

In [42]:
min_idx

[35,
 45,
 90,
 101,
 102,
 103,
 128,
 147,
 156,
 184,
 203,
 221,
 238,
 241,
 250,
 252,
 254,
 273,
 305,
 307,
 329,
 330,
 396,
 402,
 403,
 467,
 514,
 552,
 568,
 573,
 614,
 619,
 624,
 668,
 702,
 703,
 721,
 743,
 746,
 750,
 758,
 806,
 807,
 836,
 837,
 840,
 856,
 864,
 866,
 870,
 878,
 893,
 921,
 926,
 929,
 952,
 971,
 979,
 998,
 1004,
 1023,
 1030,
 1033,
 1067,
 1074,
 1118,
 1119,
 1160,
 1174,
 1217,
 1232,
 1254,
 1276,
 1299,
 1419,
 1436,
 1454,
 1455,
 1491,
 1538,
 1539,
 1551,
 1598,
 1612,
 1613,
 1631,
 1642,
 1645,
 1646,
 1703,
 1721,
 1745,
 1750,
 1771,
 1819,
 1830,
 1831,
 1849,
 1856,
 1862,
 1863,
 1908,
 1928,
 1941,
 1956,
 1957,
 1992,
 1999,
 2002,
 2006,
 2082,
 2119,
 2133,
 2178,
 2196,
 2210,
 2212,
 2265,
 2287,
 2290,
 2294,
 2318,
 2319,
 2357,
 2371,
 2408,
 2449,
 2460,
 2470,
 2519,
 2524,
 2549,
 2585,
 2591,
 2602,
 2622,
 2631,
 2648,
 2652,
 2653,
 2690,
 2692,
 2694,
 2706,
 2726,
 2728,
 2729,
 2733,
 2751,
 2764,
 2773,
 2820

In [58]:
tidx = 3112

In [59]:
dev_dataset[tidx]

{'label': 1,
 'text': 'once you get to him , save it  . 2 .  once you get to him, save it . '}

In [60]:
sentence = dev_dataset[tidx]['text']

In [61]:
inputs = tokenizer.encode_plus(sentence, return_tensors='pt', add_special_tokens=True)

In [62]:
input_ids = inputs['input_ids'].to(device)
token_type_ids = inputs['token_type_ids'].to(device)
attention = model(input_ids, token_type_ids=token_type_ids, output_attentions=True)[-1]

In [63]:
# sentence_b_start = token_type_ids[0].tolist().index(1)
input_id_list = input_ids[0].tolist() # Batch index 0
tokens = tokenizer.convert_ids_to_tokens(input_id_list) 

In [64]:
token_type_ids

tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 2]], device='cuda:0')

In [65]:
tokens

['▁once',
 '▁you',
 '▁get',
 '▁to',
 '▁him',
 '▁',
 ',',
 '▁save',
 '▁it',
 '▁',
 '.',
 '▁2',
 '▁',
 '.',
 '▁once',
 '▁you',
 '▁get',
 '▁to',
 '▁him',
 ',',
 '▁save',
 '▁it',
 '▁',
 '.',
 '<sep>',
 '<cls>']

In [66]:
model_view(attention, tokens)

<IPython.core.display.Javascript object>

In [67]:
head_view(attention, tokens)

<IPython.core.display.Javascript object>

In [68]:
outputs = model(input_ids, token_type_ids=token_type_ids)

In [69]:
outputs[0]

tensor([[-0.6618,  1.0988]], device='cuda:0', grad_fn=<AddmmBackward>)

In [70]:
logits = outputs[0]
            
# Move logits and labels to CPU
logits = logits.detach().cpu().numpy()

In [71]:
predict_content = logits.argmax(axis=-1).flatten().tolist()

In [72]:
predict_content

[1]